In [ ]:
!pip -q install langchain
!pip -q install langchain_openai
!pip -q install sqlalchemy

In [16]:
import os
from langchain.agents import create_sql_agent
from langchain.agents.agent_toolkits import SQLDatabaseToolkit
from langchain.agents.agent_types import AgentType
from langchain_openai import AzureChatOpenAI
from langchain.sql_database import SQLDatabase
from langchain.prompts.chat import ChatPromptTemplate
import sqlalchemy as sa

In [10]:
os.environ["AZURE_OPENAI_ENDPOINT"]="your endpint" # Your Azure OpenAI resource endpoint
os.environ["AZURE_OPENAI_API_KEY"]="your key" # Your Azure OpenAI resource key

os.environ["SQL_SERVER"]="localhost" # Your az SQL server name
os.environ["SQL_DB"]="northwind"
os.environ["SQL_USERNAME"]="sa" # SQL server username 
os.environ["SQL_PWD"]="password@1234" # SQL server password 

In [17]:
connection_url = sa.URL.create(
    "mssql+pymssql",
    username=os.getenv('SQL_USERNAME'),
    password=os.getenv('SQL_PWD'),
    host=os.getenv('SQL_SERVER'),
    database=os.getenv('SQL_DB'))

db_engine=sa.create_engine(connection_url)
db=SQLDatabase(db_engine)

In [ ]:
llm=AzureChatOpenAI(openai_api_version="2023-05-15", azure_deployment="gpt-35-turbo",)
sql_toolkit=SQLDatabaseToolkit(db=db,llm=llm)
sql_toolkit.get_tools()

prompt=ChatPromptTemplate.from_messages(
    [
        ("system",
        """
        you are a very intelligent AI assitasnt who is expert in identifying relevant questions from user and converting into sql queriesa to generate correcrt answer.
        Please use the below context to write the microsoft sql queries , dont use mysql queries.
        context:
        you must query against the connected database, you can use the database name as northwind.
        As an expert you must use joins whenever required.
        """
        ),
        ("user","{question}\ ai: ")
    ]
)
agent=create_sql_agent(llm=llm,toolkit=sql_toolkit,agent_type=AgentType.ZERO_SHOT_REACT_DESCRIPTION,verbose=True,max_execution_time=100,max_iterations=1000)

while True:
  question = input("Enter db query (or Enter to quit): ")
  if not question:
    break
  agent.run(prompt.format_prompt(question=question))
